In [1]:
import os
os.environ['HF_HOME'] = "/scratch/tar3kh/models/cache"
import torch 
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline
from datasets import load_dataset #datasets is huggingface's dataset package
from peft import get_peft_model, LoraConfig, TaskType
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import PIL

import lm_eval

In [2]:
tokenizer = AutoTokenizer.from_pretrained("meta-llama/Llama-3.2-3B-Instruct")
model = AutoModelForCausalLM.from_pretrained("meta-llama/Llama-3.2-3B-Instruct", device_map = "auto", torch_dtype = torch.bfloat16)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [3]:
task_manager = lm_eval.tasks.TaskManager()

In [4]:

results = lm_eval.simple_evaluate(
    model = 'hf',
    model_args = {"pretrained": model, "dtype": "bfloat16", "toeknzier": tokenizer},
    tasks = ['gsm8k_cot',  'mmlu'],
    task_manager = task_manager,
    log_samples = True, 
    batch_size = "1", 
    limit = 30, 
    random_seed = 42)

`pretrained` model kwarg is not of type `str`. Many other model arguments may be ignored. Please do not launch via accelerate or use `parallelize=True` if passing an existing model this way.
Passed an already-initialized model through `pretrained`, assuming single-process call to evaluate() or custom distributed integration
Running generate_until requests:   0%|          | 0/30 [00:00<?, ?it/s]/scratch/tar3kh/llm_course_2/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/scratch/tar3kh/llm_course_2/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:636: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True

In [5]:
results['results']

{'gsm8k_cot': {'alias': 'gsm8k_cot',
  'exact_match,strict-match': np.float64(0.5),
  'exact_match_stderr,strict-match': 0.09284766908852593,
  'exact_match,flexible-extract': np.float64(0.5),
  'exact_match_stderr,flexible-extract': 0.09284766908852593},
 'mmlu': {'acc,none': 0.6111111111111112,
  'acc_stderr,none': np.float64(0.011219896029746483),
  'alias': 'mmlu'},
 'mmlu_humanities': {'acc,none': 0.6435897435897436,
  'acc_stderr,none': np.float64(0.02350521124512561),
  'alias': ' - humanities'},
 'mmlu_formal_logic': {'alias': '  - formal_logic',
  'acc,none': 0.3,
  'acc_stderr,none': 0.0850962943396763},
 'mmlu_high_school_european_history': {'alias': '  - high_school_european_history',
  'acc,none': 0.6666666666666666,
  'acc_stderr,none': 0.08753762190648169},
 'mmlu_high_school_us_history': {'alias': '  - high_school_us_history',
  'acc,none': 0.6333333333333333,
  'acc_stderr,none': 0.08948554539839962},
 'mmlu_high_school_world_history': {'alias': '  - high_school_world_

In [6]:
# pull in the datasets and prepare them for training

budget = pd.read_csv("budget_dataset.csv")
goals = pd.read_csv("goals_dataset.csv")


In [7]:
budget['instruct_lora'] = budget.apply(
    lambda row: f"Q: {row['question']}\n\nA: ",
    axis=1
)

goals['instruct_lora'] = goals.apply(
    lambda row: f"Q: {row['question']}\n\nA: ",
    axis=1
)

In [8]:
from datasets import load_dataset, Dataset #datasets is huggingface's dataset package
budget = budget.sample(frac = 1, random_state = 42) # randomly shuffle DF
train_budget = budget[:2500]
val_budget = budget[2500:]
train_budget = Dataset.from_pandas(train_budget)
val_budget = Dataset.from_pandas(val_budget)
train_budget = train_budget.map(lambda samples: tokenizer(samples['instruct']), batched = True)
val_budget = val_budget.map(lambda samples: tokenizer(samples['instruct']), batched = True)

Map:   0%|          | 0/2500 [00:00<?, ? examples/s]

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

In [9]:
goals = goals.sample(frac = 1, random_state = 42) # randomly shuffle DF
train_goals = goals[:2500]
val_goals = goals[2500:]
train_goals = Dataset.from_pandas(train_goals)
val_goals = Dataset.from_pandas(val_goals)
train_goals = train_goals.map(lambda samples: tokenizer(samples['instruct']), batched = True)
val_goals = val_goals.map(lambda samples: tokenizer(samples['instruct']), batched = True)

Map:   0%|          | 0/2500 [00:00<?, ? examples/s]

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

In [10]:
# Prepare the model and tokenizer 
tokenizer.pad_token = tokenizer.eos_token # set padding token to EOS token
model.config.poad_token_id = tokenizer.pad_token_id # set the padding token for model

In [11]:
formatted_prompt = f"Q: {val_goals[0]['question']}\n\nA: "
inputs = tokenizer.encode(formatted_prompt, return_tensors = "pt").to(model.device)
output = model.generate(inputs, max_new_tokens = 800, pad_token_id = tokenizer.pad_token_id, do_sample = False)
generated_text = tokenizer.decode(output[0], skip_special_tokens = True)
print(generated_text)

/scratch/tar3kh/llm_course_2/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
/scratch/tar3kh/llm_course_2/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:636: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


Q: My short term goal is to save for a $1774 vacation in the next year, my medium term goal is to save for down payment for a new car, around 5227 in the next 2 or 3 years, and my long term goal is to save for a down payment for a house around 151861 in the next ten years, can you help me integrate these goals into my budget as well as where I should store these savings?

A: 1. Short-term goal: Saving for a vacation in the next year. Allocate a specific amount each month towards this goal. For example, you can set aside $147 per month for 12 months to reach your goal of $1774. You can use a separate savings account specifically for this goal. Consider opening a high-yield savings account or a money market fund to earn interest on your savings.

2. Medium-term goal: Saving for a down payment on a new car in 2-3 years. Allocate a specific amount each month towards this goal. For example, you can set aside $174 per month for 24-36 months to reach your goal of $5227. You can use a separate

In [12]:
formatted_prompt = f"Q: {val_budget[0]['question']}\n\nA: "
inputs = tokenizer.encode(formatted_prompt, return_tensors = "pt").to(model.device)
output = model.generate(inputs, max_new_tokens = 800, pad_token_id = tokenizer.pad_token_id, do_sample = False)
generated_text = tokenizer.decode(output[0], skip_special_tokens = True)
print(generated_text)

Q: I  have an income of about 53255 a year and my monthly expenses include 2208 a month in rent and utilities, a 700 car payment, $300 in food, and about 205 a month in other expenses. Using python, can you create for me a budget spreadsheet and export it to excel?

A:  Here's a Python script that creates a budget spreadsheet and exports it to Excel:

```python
import pandas as pd

# Define your income and expenses
income = 53255
rent_and_utilities = 2208
car_payment = 700
food = 300
other_expenses = 205

# Calculate your total monthly expenses
total_expenses = rent_and_utilities + car_payment + food + other_expenses

# Create a dictionary to store your income and expenses
budget = {
    'Income': [income],
    'Fixed Expenses': [rent_and_utilities, car_payment, other_expenses],
    'Variable Expenses': [food],
    'Total Expenses': [total_expenses]
}

# Create a DataFrame from the dictionary
df = pd.DataFrame(budget)

# Print the DataFrame
print(df)

# Export the DataFrame to an Excel

In [13]:
del model
torch.cuda.empty_cache()

In [14]:
tokenizer = AutoTokenizer.from_pretrained("mistralai/Ministral-8B-Instruct-2410")
model = AutoModelForCausalLM.from_pretrained("mistralai/Ministral-8B-Instruct-2410", device_map = "auto", torch_dtype = torch.bfloat16)

You are using the default legacy behaviour of the <class 'transformers.models.llama.tokenization_llama_fast.LlamaTokenizerFast'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565 - if you loaded a llama tokenizer from a GGUF file you can ignore this message.


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

In [15]:
# Prepare the model and tokenizer 
tokenizer.pad_token = tokenizer.eos_token # set padding token to EOS token
model.config.poad_token_id = tokenizer.pad_token_id # set the padding token for model

In [16]:

results2 = lm_eval.simple_evaluate(
    model = 'hf',
    model_args = {"pretrained": model, "dtype": "bfloat16", "toeknzier": tokenizer},
    tasks = ['gsm8k_cot',  'mmlu'],
    task_manager = task_manager,
    log_samples = True, 
    batch_size = "1", 
    limit = 30, 
    random_seed = 42)

`pretrained` model kwarg is not of type `str`. Many other model arguments may be ignored. Please do not launch via accelerate or use `parallelize=True` if passing an existing model this way.
Passed an already-initialized model through `pretrained`, assuming single-process call to evaluate() or custom distributed integration
Running generate_until requests: 100%|██████████| 30/30 [02:34<00:00,  5.15s/it]
fatal: not a git repository (or any parent up to mount point /sfs/gpfs)
Stopping at filesystem boundary (GIT_DISCOVERY_ACROSS_FILESYSTEM not set).


In [17]:
results2['results']

{'gsm8k_cot': {'alias': 'gsm8k_cot',
  'exact_match,strict-match': np.float64(0.6666666666666666),
  'exact_match_stderr,strict-match': 0.08753762190648169,
  'exact_match,flexible-extract': np.float64(0.7),
  'exact_match_stderr,flexible-extract': 0.0850962943396763},
 'mmlu': {'acc,none': 0.6450292397660818,
  'acc_stderr,none': np.float64(0.011026946921383438),
  'alias': 'mmlu'},
 'mmlu_humanities': {'acc,none': 0.6666666666666666,
  'acc_stderr,none': np.float64(0.022655549762135505),
  'alias': ' - humanities'},
 'mmlu_formal_logic': {'alias': '  - formal_logic',
  'acc,none': 0.5,
  'acc_stderr,none': 0.09284766908852593},
 'mmlu_high_school_european_history': {'alias': '  - high_school_european_history',
  'acc,none': 0.6333333333333333,
  'acc_stderr,none': 0.08948554539839962},
 'mmlu_high_school_us_history': {'alias': '  - high_school_us_history',
  'acc,none': 0.8,
  'acc_stderr,none': 0.07427813527082075},
 'mmlu_high_school_world_history': {'alias': '  - high_school_world

In [18]:
formatted_prompt = f"Q: {val_goals[0]['question']}\n\nA: "
inputs = tokenizer.encode(formatted_prompt, return_tensors = "pt").to(model.device)
output = model.generate(inputs, max_new_tokens = 800, pad_token_id = tokenizer.pad_token_id, do_sample = False)
generated_text = tokenizer.decode(output[0], skip_special_tokens = True)
print(generated_text)

Q: My short term goal is to save for a $1774 vacation in the next year, my medium term goal is to save for down payment for a new car, around 5227 in the next 2 or 3 years, and my long term goal is to save for a down payment for a house around 151861 in the next ten years, can you help me integrate these goals into my budget as well as where I should store these savings?

A: 1. **Budgeting for Savings:**

   - **Short Term (Vacation):**
     - Allocate a specific amount each month towards your vacation fund. For example, if you save $148 per month, you'll reach your goal in 12 months.
     - Consider setting up an automatic transfer from your checking account to your savings account each month.

   - **Medium Term (Car Down Payment):**
     - Allocate a specific amount each month towards your car down payment. For example, if you save $436 per month, you'll reach your goal in 2 years.
     - Consider setting up an automatic transfer from your checking account to your savings account ea

In [19]:
formatted_prompt = f"Q: {val_budget[0]['question']}\n\nA: "
inputs = tokenizer.encode(formatted_prompt, return_tensors = "pt").to(model.device)
output = model.generate(inputs, max_new_tokens = 800, pad_token_id = tokenizer.pad_token_id, do_sample = False)
generated_text = tokenizer.decode(output[0], skip_special_tokens = True)
print(generated_text)

Q: I  have an income of about 53255 a year and my monthly expenses include 2208 a month in rent and utilities, a 700 car payment, $300 in food, and about 205 a month in other expenses. Using python, can you create for me a budget spreadsheet and export it to excel?

A:  To create a budget spreadsheet and export it to Excel using Python, you can use the `pandas` library to handle the data and `openpyxl` to write the data to an Excel file. Below is a step-by-step guide and the corresponding Python code to achieve this:

1. **Install the necessary libraries**:
   You need to install `pandas` and `openpyxl` if you haven't already. You can install them using pip:
   ```sh
   pip install pandas openpyxl
   ```

2. **Create the budget spreadsheet**:
   Here's a Python script that creates a budget spreadsheet and exports it to an Excel file:

   ```python
   import pandas as pd

   # Define your income and expenses
   income = 53255
   monthly_expenses = {
       'Rent and Utilities': 2208,
  

## Few Shot Prompting for Goals

In [24]:
del model
torch.cuda.empty_cache()

In [25]:
os.environ['HF_HOME'] = "Documents/MSDS/DS5002/trained_lora_model_project/best_model"

In [26]:
tokenizer = AutoTokenizer.from_pretrained("TheFinAI/Fino1-8B")
model = AutoModelForCausalLM.from_pretrained("TheFinAI/Fino1-8B", device_map = "auto", torch_dtype = torch.bfloat16)

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

In [27]:
test_goals = goals[2500:]

In [28]:
pipe = pipeline(
    "text-generation", 
    model=model, 
    torch_dtype=torch.bfloat16, 
    device_map="auto", 
    tokenizer = tokenizer, 
    max_new_tokens = 750,
    do_sample = False,
    temperature = 0
)

Device set to use cuda:0


In [29]:
def few_shot_goal(df3,pipe,n = 1,q = 10):
    examples = []
    for i in range(n):
        instruct = df3['instruct'].iloc[i]
        examples.append(instruct)
    examples.append(df3.iloc[q]['question_1'])
    examples = "\n\n".join(examples)
    text = pipe(examples)
    print(text[0]['generated_text'])

In [30]:
few_shot_goal(test_goals,pipe,n = 3,q=10)

/scratch/tar3kh/llm_course_2/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:636: UserWarning: `do_sample` is set to `False`. However, `top_p` is set to `0.9` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `top_p`.
  warnings.warn(


Q: My short term goal is to save for a $1774 vacation in the next year, my medium term goal is to save for down payment for a new car, around 5227 in the next 2 or 3 years, and my long term goal is to save for a down payment for a house around 151861 in the next ten years, can you help me integrate these goals into my budget as well as where I should store these savings?

A: Lets think step by step. 1. Short-Term Goal: $1774 Vacation (1 Year)
Timeline: 12 months
Monthly Savings Needed: 1774 / 12 = 148.0

Best Storage Option: High-yield savings account (HYSA)
Easy access
Earns some interest
Safe from market fluctuations,

2. Medium-Term Goal: $5227  Car Down Payment (2–3 Years)
Timeline Options:
2 years (24 months) → $218.0/month
3 years (36 months) → $145.0/month
Best Storage Option: HYSA or conservative investment
If comfortable with some risk, a mix of HYSA + conservative investments (e.g., CDs, bond ETFs)
If risk-averse, keep it in an HYSA,

3. Long-Term Goal: $151861   House Down P

In [31]:
results3 = lm_eval.simple_evaluate(
    model = 'hf',
    model_args = {"pretrained": model, "dtype": "bfloat16", "toeknzier": tokenizer},
    tasks = ['gsm8k_cot',  'mmlu'],
    task_manager = task_manager,
    log_samples = True, 
    batch_size = "1", 
    limit = 30, 
    random_seed = 42)

`pretrained` model kwarg is not of type `str`. Many other model arguments may be ignored. Please do not launch via accelerate or use `parallelize=True` if passing an existing model this way.
Passed an already-initialized model through `pretrained`, assuming single-process call to evaluate() or custom distributed integration
Running generate_until requests:   0%|          | 0/30 [00:00<?, ?it/s]/scratch/tar3kh/llm_course_2/lib/python3.11/site-packages/transformers/generation/configuration_utils.py:631: UserWarning: `do_sample` is set to `False`. However, `temperature` is set to `0.6` -- this flag is only used in sample-based generation modes. You should set `do_sample=True` or unset `temperature`.
  warnings.warn(
Running generate_until requests: 100%|██████████| 30/30 [03:09<00:00,  6.32s/it]
fatal: not a git repository (or any parent up to mount point /sfs/gpfs)
Stopping at filesystem boundary (GIT_DISCOVERY_ACROSS_FILESYSTEM not set).


In [32]:
results3['results']

{'gsm8k_cot': {'alias': 'gsm8k_cot',
  'exact_match,strict-match': np.float64(0.6333333333333333),
  'exact_match_stderr,strict-match': 0.0894855453983996,
  'exact_match,flexible-extract': np.float64(0.6333333333333333),
  'exact_match_stderr,flexible-extract': 0.0894855453983996},
 'mmlu': {'acc,none': 0.6684210526315789,
  'acc_stderr,none': np.float64(0.010724424663842536),
  'alias': 'mmlu'},
 'mmlu_humanities': {'acc,none': 0.7076923076923077,
  'acc_stderr,none': np.float64(0.02268555050327971),
  'alias': ' - humanities'},
 'mmlu_formal_logic': {'alias': '  - formal_logic',
  'acc,none': 0.5333333333333333,
  'acc_stderr,none': 0.09264111117062017},
 'mmlu_high_school_european_history': {'alias': '  - high_school_european_history',
  'acc,none': 0.6333333333333333,
  'acc_stderr,none': 0.08948554539839962},
 'mmlu_high_school_us_history': {'alias': '  - high_school_us_history',
  'acc,none': 0.7333333333333333,
  'acc_stderr,none': 0.08211756827352532},
 'mmlu_high_school_world